# Imports

In [269]:
import numpy as np
import pandas as pd
import random

import matplotlib.pyplot as plt
import seaborn as sns

import kaggle_environments
from kaggle_environments import make, evaluate

# My agents

## 

2.1

In [352]:
%%writefile rock_agent.py

#0 - rock
#1 - paper
#2 - scissors
def rock_agent(observation, configuration):
    return 0

Overwriting rock_agent.py


In [357]:
evaluate(
    "rps", #environment to use - no need to change
    ["rock_agent.py", "paper"], #agents to evaluate
    configuration={"episodeSteps": 1000} #number of episodes 
)

[[-999.0, 999.0]]

## 

2.2

In [401]:
%%writefile paper_agent.py

#0 - rock
#1 - paper
#2 - scissors
def paper_agent(observation, configuration):
    return 1

Overwriting paper_agent.py


In [403]:
evaluate(
    "rps", #environment to use - no need to change
    ["rock_agent.py", "paper_agent.py"], #agents to evaluate
    configuration={"episodeSteps": 1000} #number of episodes 
)

[[-999.0, 999.0]]

## 

2.3

In [337]:
%%writefile copy_opponent.py
import random
#Example 
def copy_opponent(observation, configuration):
    #in case we have information about opponent last move
    if observation.step > 0:
        return observation.lastOpponentAction
    #initial step
    else:
        return random.randrange(0, configuration.signs)

Overwriting copy_opponent.py


In [360]:
evaluate(
    "rps", #environment to use - no need to change
    ["rock_agent.py", "copy_opponent"], #agents to evaluate
    configuration={"episodeSteps": 1000} #number of episodes 
)

[[0, 0]]

## 

2.4

In [338]:
%%writefile absolute_random.py

# the most simple agenty
import random

def absolute_random(obs, conf):
    return random.randint(0, 2)

Overwriting absolute_random.py


In [405]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["paper_agent.py", "absolute_random.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[0, 0]]


## 

2.5

In [340]:
%%writefile no_rock.py

# paper-scissors agent
import random

def no_rock(obs, conf):
    return random.randint(1, 2)

Overwriting no_rock.py


In [342]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["no_rock.py", "rock_agent.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[49.0, -49.0]]


## 

2.6

In [394]:
%%writefile no_scissors.py

# paper-scissors agent
import random

def no_scissors(obs, conf):
    return random.randint(0, 1)

Overwriting no_scissors.py


In [396]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["rock_agent.py", "no_scissors.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[-507.0, 507.0]]


## 

2.7

In [343]:
%%writefile copy_opponent_except_scissors.py
import random
# opponent copy apart from scissors
def copy_opponent_except_scissors(observation, configuration):
    #in case we have information about opponent last move
    if observation.step > 0:
        return observation.lastOpponentAction
    #initial step
    else:
        return random.randrange(0, 1)

Writing copy_opponent_except_scissors.py


In [347]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["copy_opponent.py", "copy_opponent_except_scissors.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[0, 0]]


## 

2.8

In [406]:
%%writefile copy_opponent_except_rock.py
import random
# opponent copy apart from scissors
def copy_opponent_except_rock(observation, configuration):
    #in case we have information about opponent last move
    if observation.step > 0:
        return observation.lastOpponentAction
    #initial step
    else:
        return random.randrange(1, 2)

Writing copy_opponent_except_rock.py


In [407]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["copy_opponent_except_rock.py", "copy_opponent_except_scissors.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[0, 0]]


## 

2.9

In [371]:
%%writefile counter_react.py
import random
import kaggle_environments
last_react_action = None
def counter_react(observation, configuration):
    global last_counter_action
    if observation.step >= 0 or observation.step is None:
        last_counter_action = random.randrange(0, configuration.signs)
    elif get_score(last_counter_action, observation.lastOpponentAction) == 1:
        last_counter_action = (last_counter_action + 2) % configuration.signs
    else:
        last_counter_action = (observation.lastOpponentAction + 1) % configuration.signs

    return last_counter_action

Overwriting counter_react.py


In [372]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["counter_react.py", "copy_opponent.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[38.0, -38.0]]


## 

2.10

In [376]:
%%writefile crazyfrog.py

import numpy as np
import collections

def crazyfrog(observation, configuration):
    k = 2
    global table, action_seq
    if observation.step % 250 == 0: # refresh table every 250 steps
        action_seq, table = [], collections.defaultdict(lambda: [1, 1, 1])    
    if len(action_seq) <= 2 * k + 1:
        action = int(np.random.randint(3))
        if observation.step > 0:
            action_seq.extend([observation.lastOpponentAction, action])
        else:
            action_seq.append(action)
        return action
    # update table
    key = ''.join([str(a) for a in action_seq[:-1]])
    table[key][observation.lastOpponentAction] += 1
    # update action seq
    action_seq[:-2] = action_seq[2:]
    action_seq[-2] = observation.lastOpponentAction
    # predict opponent next move
    key = ''.join([str(a) for a in action_seq[:-1]])
    if observation.step < 500:
        next_opponent_action_pred = np.argmax(table[key])
    else:
        scores = np.array(table[key])
        next_opponent_action_pred = np.random.choice(3, p=scores/scores.sum()) # add stochasticity for second part of the game
    # make an action
    action = (next_opponent_action_pred + 1) % 3
    # if high probability to lose -> let's surprise our opponent with sudden change of our strategy
    if observation.step > 900:
        action = next_opponent_action_pred
    action_seq[-1] = action
    return int(action)

Overwriting crazyfrog.py


In [377]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["crazyfrog.py", "copy_opponent_except_scissors.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[593.0, -593.0]]


## 

2.11

In [378]:
%%writefile statist.py

action_histogram = {}

def statist(observation, configuration):
    global action_histogram
    if observation.step == 0:
        action_histogram = {}
        return
    action = observation.lastOpponentAction
    if action not in action_histogram:
        action_histogram[action] = 0
    action_histogram[action] += 1
    mode_action = None
    mode_action_count = None
    for k, v in action_histogram.items():
        if mode_action_count is None or v > mode_action_count:
            mode_action = k
            mode_action_count = v
            continue

    return (mode_action + 1) % configuration.signs

Overwriting statist.py


In [379]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["crazyfrog.py", "statist.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[350.0, -350.0]]


## 

2.12

In [380]:
%%writefile opponent_matrix.py

import numpy as np
import pandas as pd
import random

T = np.zeros((3, 3))
P = np.zeros((3, 3))

# a1 is the action of the opponent 1 step ago
# a2 is the action of the opponent 2 steps ago
a1, a2 = None, None

def transition_agent(observation, configuration):
    global T, P, a1, a2
    if observation.step > 1:
        a1 = observation.lastOpponentAction
        T[a2, a1] += 1
        P = np.divide(T, np.maximum(1, T.sum(axis=1)).reshape(-1, 1))
        a2 = a1
        if np.sum(P[a1, :]) == 1:
            return int((np.random.choice(
                [0, 1, 2],
                p=P[a1, :]
            ) + 1) % 3)
        else:
            return int(np.random.randint(3))
    else:
        if observation.step == 1:
            a2 = observation.lastOpponentAction
        return int(np.random.randint(3))

Writing opponent_matrix.py


In [381]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["crazyfrog.py", "opponent_matrix.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[-102.0, 102.0]]


## 

2.13

In [391]:
%%writefile geometry.py
import operator
import numpy as np
import cmath
from typing import List
from collections import namedtuple
import traceback
import sys


basis = np.array(
    [1, cmath.exp(2j * cmath.pi * 1 / 3), cmath.exp(2j * cmath.pi * 2 / 3)]
)


HistMatchResult = namedtuple("HistMatchResult", "idx length")


def find_all_longest(seq, max_len=None) -> List[HistMatchResult]:
    """
    Find all indices where end of `seq` matches some past.
    """
    result = []

    i_search_start = len(seq) - 2

    while i_search_start > 0:
        i_sub = -1
        i_search = i_search_start
        length = 0

        while i_search >= 0 and seq[i_sub] == seq[i_search]:
            length += 1
            i_sub -= 1
            i_search -= 1

            if max_len is not None and length > max_len:
                break

        if length > 0:
            result.append(HistMatchResult(i_search_start + 1, length))

        i_search_start -= 1

    result = sorted(result, key=operator.attrgetter("length"), reverse=True)

    return result


def probs_to_complex(p):
    return p @ basis


def _fix_probs(probs):
    """
    Put probs back into triangle. Sometimes this happens due to rounding errors or if you
    use complex numbers which are outside the triangle.
    """
    if min(probs) < 0:
        probs -= min(probs)

    probs /= sum(probs)

    return probs


def complex_to_probs(z):
    probs = (2 * (z * basis.conjugate()).real + 1) / 3
    probs = _fix_probs(probs)
    return probs


def z_from_action(action):
    return basis[action]


def sample_from_z(z):
    probs = complex_to_probs(z)
    return np.random.choice(3, p=probs)


def bound(z):
    return probs_to_complex(complex_to_probs(z))


def norm(z):
    return bound(z / abs(z))


class Pred:
    def __init__(self, *, alpha):
        self.offset = 0
        self.alpha = alpha
        self.last_feat = None

    def train(self, target):
        if self.last_feat is not None:
            offset = target * self.last_feat.conjugate()   # fixed

            self.offset = (1 - self.alpha) * self.offset + self.alpha * offset

    def predict(self, feat):
        """
        feat is an arbitrary feature with a probability on 0,1,2
        anything which could be useful anchor to start with some kind of sensible direction
        """
        feat = norm(feat)

        # offset = mean(target - feat)
        # so here we see something like: result = feat + mean(target - feat)
        # which seem natural and accounts for the correlation between target and feat
        # all RPSContest bots do no more than that, just in a hidden way
        
        result = feat * self.offset

        self.last_feat = feat

        return result
    
    
class BaseAgent:
    def __init__(self):
        self.my_hist = []
        self.opp_hist = []
        self.my_opp_hist = []
        self.outcome_hist = []
        self.step = None

    def __call__(self, obs, conf):
        try:
            if obs.step == 0:
                action = np.random.choice(3)
                self.my_hist.append(action)
                return action

            self.step = obs.step

            opp = int(obs.lastOpponentAction)
            my = self.my_hist[-1]

            self.my_opp_hist.append((my, opp))
            self.opp_hist.append(opp)

            outcome = {0: 0, 1: 1, 2: -1}[(my - opp) % 3]
            self.outcome_hist.append(outcome)

            action = self.action()

            self.my_hist.append(action)

            return action
        except Exception:
            traceback.print_exc(file=sys.stderr)
            raise

    def action(self):
        pass


class Agent(BaseAgent):
    def __init__(self, alpha=0.01):
        super().__init__()

        self.predictor = Pred(alpha=alpha)

    def action(self):
        self.train()

        pred = self.preds()

        return_action = sample_from_z(pred)

        return return_action

    def train(self):
        last_beat_opp = z_from_action((self.opp_hist[-1] + 1) % 3)
        self.predictor.train(last_beat_opp)

    def preds(self):
        hist_match = find_all_longest(self.my_opp_hist, max_len=20)

        if not hist_match:
             return 0

        feat = z_from_action(self.opp_hist[hist_match[0].idx])

        pred = self.predictor.predict(feat)

        return pred
    
    
agent = Agent()


def call_agent(obs, conf):
    return agent(obs, conf)

Writing geometry.py


In [392]:
results = evaluate(
    "rps", #environment to use - no need to change
    ["crazyfrog.py", "geometry.py"], #agents to evaluate
#     ["copy_opponent.py", "rock_agent.py"],
#     num_episodes=5,
    configuration={"episodeSteps": 1000} #number of episodes 
)
print(results)

[[-36.0, 36.0]]


## 

2.14

In [285]:
# %%writefile no_repeat.py
# from random import sample
# # 1. The agent is not use the same action twice till all of three is used
# # 2. The order is chosen randomly and recreated after every 3rd step
# counter = 0
# def no_repeat(observation, configuration):
#     global counter
#     if observation.step is None:
#         action = random.randrange(0, configuration.signs)
#     elif observation.step % 3 == 0:
#         counter = 0
#         lst = random.sample(range(0,3), configuration.signs)
#         action = lst[counter]
#         counter =+ 1
#     return action

In [ ]:
# results = evaluate(
#     "rps", #environment to use - no need to change
#     ["no_repeat.py", "opponent_matrix.py"], #agents to evaluate
# #     ["copy_opponent.py", "rock_agent.py"],
# #     num_episodes=5,
#     configuration={"episodeSteps": 1000} #number of episodes 
# )
# print(results)

# Visual test

In [15]:
from kaggle_environments import evaluate, make, utils
env = make("rps", debug=True)
env.render()

In [397]:
env.reset()

env.run(["crazyfrog.py", "geometry.py"])
env.render(mode="ipython", width=500, height=400)

☔☔☔